In [ ]:
#hide
%reload_ext autoreload
%autoreload 2

In [ ]:
from peptdeep.rescore.percolator import Percolator
import os

In [ ]:
#hide
from alphabase.io.psm_reader import psm_reader_provider
reader = psm_reader_provider.get_reader('alphapept', fdr=1, keep_decoy=True)
reader.import_file(os.path.expanduser('~/Workspace/Data/HeLa_500ng/HeLa_DDA_tims.ms_data.hdf'))
select_col = 'spec_idx' #scan no
idx = reader.psm_df.groupby(select_col)['score'].idxmax()
psm_df = reader.psm_df.loc[idx]
psm_df.drop_duplicates([select_col,'sequence','mods'],inplace=True)
psm_df.sort_values(select_col)

rt  spec_idx  query_id  mobility      score  precursor_mz  \
23191    2.358303       498     24180  0.855388  18.030514    549.211975   
259410   2.534062       544     63144  0.723922  15.925869    513.581757   
232003   2.534062       552     83224  0.760560  23.631358    582.593603   
232014   2.534062       553     83225  0.797198  23.708700    582.593603   
15685    2.686883       579     20367  0.825216  20.431965    524.210003   
...           ...       ...       ...       ...        ...           ...   
182107  20.927873     55766     61462  1.014871  32.743932    760.420748   
273894  20.252299     55798    118520  1.000862  26.112362    752.657436   
193563  20.174618     55810     68075  0.843534  17.422746    530.296337   
295168  20.252299     55814    126909  1.061207  21.498282    850.729220   
233267  20.291160     55829     89127  1.104310  15.476523    904.958702   

        charge       raw_name                 sequence  \
23191        2  HeLa_DDA_tims                NMMAACDPR   
259410       3  HeLa_DDA_tims      AEGGGGGGRPGAPAAGDGK   
232003       3  HeLa_DDA_tims        DSRPSQAAGDNQGDEAK   
232014       3  HeLa_DDA_tims        DSRPSQAAGDNQGDEAK   
15685        2  HeLa_DDA_tims                YDDMAAAMK   
...        ...            ...                      ...   
182107       2  HeLa_DDA_tims          FGANAILGVSLAVCK   
273894       3  HeLa_DDA_tims     HNDDEQYAWESSAGGSFTVR   
193563       3  HeLa_DDA_tims          THINIVVIGHVDSGK   
295168       3  HeLa_DDA_tims  LCYVALDFEQEMATAASSSSLEK   
233267       2  HeLa_DDA_tims        SQVFSTAADGQTQVEIK   

                                             mods mod_sites  decoy  nAA  \
23191   Oxidation@M;Oxidation@M;Carbamidomethyl@C     2;3;6      0    9   
259410                                                           0   19   
232003                                                           0   17   
232014                                                           0   17   
15685                     Oxidation@M;Oxidation@M       4;8      0    9   
...                                           ...       ...    ...  ...   
182107                          Carbamidomethyl@C        14      0   15   
273894                                                           0   20   
193563                                                           0   15   
295168                          Carbamidomethyl@C         2      0   23   
233267                                                           0   17   

         rt_norm         ccs  
23191   0.112478  346.921480  
259410  0.120861  438.829896  
232003  0.120861  460.551566  
232014  0.120861  482.737389  
15685   0.128150  334.882727  
...          ...         ...  
182107  0.998146  410.179878  
273894  0.965925  604.983872  
193563  0.962220  511.192917  
295168  0.965925  641.007039  
233267  0.967778  445.683841  

[39597 rows x 15 columns]

In [ ]:
#hide
from peptdeep.settings import global_settings
global_settings['percolator']['multiprocessing'] = False
perc = Percolator()
perc.feature_extractor.require_model_tuning = True
perc.feature_extractor.model_mgr.psm_num_to_train_ms2 = 1000
perc.feature_extractor.model_mgr.epoch_to_train_ms2 = 2
perc.feature_extractor.model_mgr.warmup_epoch_to_train_ms2 = 1
perc.feature_extractor.model_mgr.psm_num_to_train_rt_ccs = 1000
perc.feature_extractor.model_mgr.epoch_to_train_rt_ccs = 2
perc.feature_extractor.model_mgr.warmup_epoch_to_train_rt_ccs = 1
perc_df = perc.extract_features(psm_df, 
    ms2_file_type='alphapept', 
    ms2_file_dict={
        'HeLa_DDA_tims':
        os.path.expanduser('~/Workspace/Data/HeLa_500ng/HeLa_DDA_tims.ms_data.hdf')
    }
)
perc_df

2022-07-13 06:28:25> Fine-tuning models ...
2022-07-13 06:28:25> Preparing for fine-tuning ...


100%|██████████| 1/1 [00:34<00:00, 34.11s/it]

2022-07-13 06:29:00> Fine-tuning ...


2022-07-13 06:29:56> Fine-tuning done
2022-07-13 06:29:56> Extracting peptdeep features ...


100%|██████████| 1/1 [03:48<00:00, 228.59s/it]

2022-07-13 06:33:45> Finish extracting features


rt  spec_idx  query_id  mobility      score  precursor_mz  \
0      14.811912     36534     17809  0.821983  15.713466    507.243437   
1       5.562778      6129      7992  0.760560  12.402889    416.714580   
2       7.350258     11042     10657  0.779957  17.021423    448.711079   
3       8.632784     15729     10209  0.796121  15.945227    444.249470   
4       6.961679     10480     10770  0.825216  13.793756    449.721042   
...          ...       ...       ...       ...        ...           ...   
39592  19.125378     50704    130544  1.000862  36.460732    943.805461   
39593  14.850783     36559    132333  1.036422  13.597653   1041.168981   
39594  20.019165     53498    131110  1.008405  16.411243    974.187899   
39595   9.254545     17278    132113  0.978233  27.021416    772.590030   
39596  16.405245     42826    133009  1.084914  16.215382   1090.873164   

       charge       raw_name                     sequence               mods  \
0           2  HeLa_DDA_tims                      YNLDFWR                      
1           2  HeLa_DDA_tims                      CLVAVDR  Carbamidomethyl@C   
2           2  HeLa_DDA_tims                      FPDENFK                      
3           2  HeLa_DDA_tims                      ILEEDLR                      
4           2  HeLa_DDA_tims                      YCDSLLK  Carbamidomethyl@C   
...       ...            ...                          ...                ...   
39592       3  HeLa_DDA_tims  EGTDSSQGIPQLVSNISACQVIAEAVR  Carbamidomethyl@C   
39593       3  HeLa_DDA_tims  FTDFKLDGTGYGDYVKIYDGLEENPHK                      
39594       3  HeLa_DDA_tims  GLYGIKDDVFLSVPCILGQNGISDLVK  Carbamidomethyl@C   
39595       4  HeLa_DDA_tims  ATLELTHNWGTEDDETQSYHNGNSDPR                      
39596       3  HeLa_DDA_tims  IITNVIDQDIHLLGCHMINYFHTLFDK  Carbamidomethyl@C   

       ... matched_yion_rel_to_pred  pred_yion_rel_to_matched  pep_z1  pep_z2  \
0      ...                 1.000000                  0.724919       0       1   
1      ...                 0.000000                  0.000000       0       1   
2      ...                 1.000000                  0.326317       0       1   
3      ...                 1.000000                  0.626589       0       1   
4      ...                 1.000000                  0.890279       0       1   
...    ...                      ...                       ...     ...     ...   
39592  ...                 0.993290                  0.996302       0       0   
39593  ...                 0.000000                  0.000000       0       0   
39594  ...                 1.000000                  0.789969       0       0   
39595  ...                 0.789246                  0.227057       0       0   
39596  ...                 0.000000                  0.000000       0       0   

       pep_z3  pep_z4  pep_z5  pep_z6  pep_z_gt_6  mod_num  
0           0       0       0       0           0        0  
1           0       0       0       0           0        0  
2           0       0       0       0           0        0  
3           0       0       0       0           0        0  
4           0       0       0       0           0        0  
...       ...     ...     ...     ...         ...      ...  
39592       1       0       0       0           0        0  
39593       1       0       0       0           0        0  
39594       1       0       0       0           0        0  
39595       0       1       0       0           0        0  
39596       1       0       0       0           0        0  

[39597 rows x 88 columns]

In [ ]:
#hide
df = perc_df.copy()
perc.cv_fold = 2
df = perc.re_score(df)
df

2022-07-13 06:33:45> [PERC] 24142 target PSMs at 0.01 psm-level FDR
2022-07-13 06:33:45> [PERC] Iteration 1 of Percolator ...
2022-07-13 06:33:46> [PERC] 28581 target PSMs at 0.01 psm-level FDR
2022-07-13 06:33:46> [PERC] Iteration 2 of Percolator ...
2022-07-13 06:33:47> [PERC] 30523 target PSMs at 0.01 psm-level FDR
2022-07-13 06:33:47> [PERC] Iteration 3 of Percolator ...
2022-07-13 06:33:48> [PERC] 31091 target PSMs at 0.01 psm-level FDR
2022-07-13 06:33:48> [PERC] Iteration 4 of Percolator ...
2022-07-13 06:33:49> [PERC] 31303 target PSMs at 0.01 psm-level FDR
2022-07-13 06:33:49> [PERC] Iteration 5 of Percolator ...
2022-07-13 06:33:51> [PERC] 31344 target PSMs at 0.01 psm-level FDR
2022-07-13 06:33:51> [PERC] 31344 target PSMs at 0.01 psm-level FDR


rt  spec_idx  query_id  mobility      score  precursor_mz  \
0      12.791189     29252    119942  1.222845  50.764368   1144.554422   
1      11.314310     24155    121151  1.256250  54.910542   1160.558864   
2      12.791189     29395    119936  1.222845  49.183957   1144.554422   
3      10.575867     21750    129197  0.976078  39.340241    903.773833   
4      15.161719     37924    118788  1.236853  58.482517   1131.053869   
...          ...       ...       ...       ...        ...           ...   
39592  20.135763     55029     60339  0.989009  13.609224    754.901054   
39593  20.252299     54523     76726  1.089224  11.434402    839.930720   
39594  18.853359     50807     65389  1.019181  12.835001    781.411607   
39595  20.058032     54574     65106  1.052586  13.444099    779.913662   
39596  20.058032     53540     97419  1.109698  19.833569    953.484615   

       charge       raw_name                     sequence         mods  ...  \
0           2  HeLa_DDA_tims        VIAINVDDPDAANYNDINDVK               ...   
1           2  HeLa_DDA_tims    AAAASAAEAGIATTGTEDSDDALLK               ...   
2           2  HeLa_DDA_tims        VIAINVDDPDAANYNDINDVK               ...   
3           3  HeLa_DDA_tims  LGQHVVGMAPLSVGSLDDEPGGEAETK  Oxidation@M  ...   
4           2  HeLa_DDA_tims   GGMGSGGLATGIAGGLAGMGGIQNEK               ...   
...       ...            ...                          ...          ...  ...   
39592       2  HeLa_DDA_tims                RKDMTPSAQVTFK               ...   
39593       2  HeLa_DDA_tims              FHANRAHSRESPGGR               ...   
39594       2  HeLa_DDA_tims          KSGGGASGKSGSGAGGLAR               ...   
39595       2  HeLa_DDA_tims              AANINGSQVKRGSEK               ...   
39596       2  HeLa_DDA_tims        AQAAAPRERGGGGGGAGGRPR               ...   

      matched_yion_rel_to_pred  pred_yion_rel_to_matched  pep_z1  pep_z2  \
0                     0.981400                  0.869639       0       1   
1                     0.604777                  0.995302       0       1   
2                     0.978108                  0.869639       0       1   
3                     0.973934                  0.872790       0       0   
4                     0.905422                  0.942018       0       1   
...                        ...                       ...     ...     ...   
39592                 0.000000                  0.000000       0       1   
39593                 0.000000                  0.000000       0       1   
39594                 0.000000                  0.000000       0       1   
39595                 0.000000                  0.000000       0       1   
39596                 0.000000                  0.000000       0       1   

       pep_z3  pep_z4  pep_z5  pep_z6  pep_z_gt_6  mod_num  
0           0       0       0       0           0        0  
1           0       0       0       0           0        0  
2           0       0       0       0           0        0  
3           1       0       0       0           0        1  
4           0       0       0       0           0        0  
...       ...     ...     ...     ...         ...      ...  
39592       0       0       0       0           0        0  
39593       0       0       0       0           0        0  
39594       0       0       0       0           0        0  
39595       0       0       0       0           0        0  
39596       0       0       0       0           0        0  

[39597 rows x 88 columns]

In [ ]:
import plotly.graph_objs as go
from plotly.offline import init_notebook_mode
init_notebook_mode()
def plot_score_dist(df, x='ml_score'):
    fig = go.Figure()
    for decoy, df_group in df.groupby('decoy'):
        fig.add_histogram(x=df_group[x], name='decoy' if decoy else 'target')
    return fig

In [ ]:
plot_score_dist(df, 'ml_score')

In [ ]:
plot_score_dist(df, 'mobility_delta')

In [ ]:
from matplotlib_venn import venn2
from peptdeep.rescore.fdr import calc_fdr_for_df
df_fdr = df[(df.fdr<0.01)&(df.decoy==0)]
ap_df = calc_fdr_for_df(df, 'score')
ap_df = ap_df[(ap_df.fdr<0.01)&(ap_df.decoy==0)]
venn2(
    [set(df_fdr.sequence.values), set(ap_df.sequence.values)],
    ['peptdeep\nAlphaPept','AlphaPept_xtandem']
)